In [3]:
import requests
from xml.etree import ElementTree
from datetime import datetime
import utm
from unidecode import unidecode

def convert_from_utm(easting, northing, zone, letter):
    return utm.to_latlon(easting, northing, zone, letter)

def convert_to_utf8(s):
    return unidecode(s.replace("Ø", "n.").replace("´","").replace("'",""))

In [4]:
response = requests.get("https://informo.madrid.es/informo/tmadrid/pm.xml")
root = ElementTree.fromstring(response.content)

In [5]:
fecha = root[0].text
print(fecha)
fecha_formateada = datetime.strptime(fecha, "%d/%m/%Y %H:%M:%S").strftime("%Y-%m-%dT%H:%M:%SZ")
print(fecha_formateada)

13/04/2023 17:30:05
2023-04-13T17:30:05Z


In [6]:
out = []
for pm in root[1:-1]:
    d = {}
    for i in pm:
        d[i.tag] = i.text
    out.append(d)

In [7]:
print("Hay ", len(out), " medidas en el XML")

Hay  4566  medidas en el XML


In [9]:
print(out[0])    

{'idelem': '3409', 'descripcion': 'SEPULVEDA Ø118 N-S (CEBREROS-CJAL. FCO. J. JIMENEZ)', 'accesoAsociado': '240102', 'intensidad': '42', 'ocupacion': '0', 'carga': '1', 'nivelServicio': '0', 'intensidadSat': '3000', 'error': 'N', 'subarea': '1718', 'st_x': '436004,103195086', 'st_y': '4472588,47356732'}


### Formatear datos antes de enviarlos

In [10]:
for pm in out:
    # Convertir de String a Integer
    try:
        pm['intensidad'] = int(pm['intensidad'])
    except KeyError:
        pass
    except:
        del pm['intensidad']
        
    try:
        pm['ocupacion'] = int(pm['ocupacion'])
    except KeyError:
        pass
    except:
        del pm['ocupacion']
            
    try:
        pm['carga'] = int(pm['carga'])
    except KeyError:
        pass
    except:
        del pm['carga']
        
    try:
        pm['nivelServicio'] = int(pm['nivelServicio'])
    except KeyError:
        pass
    except:
        del pm['nivelServicio']
        
    try:
        pm['intensidadSat'] = int(pm['intensidadSat'])
    except KeyError:
        pass
    except:
        del pm['intensidadSat']
        
    
    # Formatear fecha
    pm['fecha_hora'] = fecha_formateada
    
    # Formatear coordenadas
    pm['st_x'] = float(pm['st_x'].replace(",","."))
    pm['st_y'] = float(pm['st_y'].replace(",","."))

    
    # Covertir coordenadas
    try:
        lat, lon = convert_from_utm(pm['st_x'], pm['st_y'], 30, "T")
        pm['coordenadas'] = {"lat":lat, "lon":lon}
        del pm['st_x']
        del pm['st_y']
    except KeyError:
        pass
    except Exception as e:
        print("ERROR COORDENADAS", e)
        del pm['coordenadas']
        
    
    # Formatear descripción
    try:
        pm['descripcion'] = convert_to_utf8(pm['descripcion'])
    except KeyError:
        pass
    except Exception as e:
        print("ERROR DESCRIPCION", e)
        del pm['descripcion']
        
    
    
    

In [11]:
print("Elementos después del formateo: ", len(out))
print(out[0])

Elementos después del formateo:  4566
{'idelem': '3409', 'descripcion': 'SEPULVEDA n.118 N-S (CEBREROS-CJAL. FCO. J. JIMENEZ)', 'accesoAsociado': '240102', 'intensidad': 42, 'ocupacion': 0, 'carga': 1, 'nivelServicio': 0, 'intensidadSat': 3000, 'error': 'N', 'subarea': '1718', 'fecha_hora': '2023-04-13T17:30:05Z', 'coordenadas': {'lat': 40.401447264855946, 'lon': -3.7541516712567753}}


### Enviar datos a Elastic con POST

In [65]:
url = "https://icai.es.europe-west2.gcp.elastic-cloud.com:9243/"
username = "admin"
password = "comillas"
index = "trafico-madrid"
headers = {"Content-Type": "application/json"}

for pm in out:
    data = str(pm).replace("'", "\"")
    response = requests.post(url+index+"/_doc", data = data, headers = headers, auth=(username, password))


ReadTimeout: HTTPSConnectionPool(host='icai.es.europe-west2.gcp.elastic-cloud.com', port=9243): Read timed out. (read timeout=None)

### Creación de NDJSON para enviar muchos datos simultáneamente

In [12]:
ndjson = ""

for pm in out:
    ndjson = ndjson + '{"index": {"_index" : "trafico-madrid"}}\n'
    data = str(pm).replace("'", "\"")
    ndjson = ndjson + data + "\n"

print(ndjson)

{"index": {"_index" : "trafico-madrid"}}
{"idelem": "3409", "descripcion": "SEPULVEDA n.118 N-S (CEBREROS-CJAL. FCO. J. JIMENEZ)", "accesoAsociado": "240102", "intensidad": 42, "ocupacion": 0, "carga": 1, "nivelServicio": 0, "intensidadSat": 3000, "error": "N", "subarea": "1718", "fecha_hora": "2023-04-13T17:30:05Z", "coordenadas": {"lat": 40.401447264855946, "lon": -3.7541516712567753}}
{"index": {"_index" : "trafico-madrid"}}
{"idelem": "4739", "descripcion": "CJAL. FCO. J. JIMENEZ n.126 E-O (BERLANAS-SEPULVEDA)", "accesoAsociado": "240101", "intensidad": 85, "ocupacion": 1, "carga": 7, "nivelServicio": 0, "intensidadSat": 1500, "error": "N", "subarea": "1718", "fecha_hora": "2023-04-13T17:30:05Z", "coordenadas": {"lat": 40.399707541055946, "lon": -3.7537194086223162}}
{"index": {"_index" : "trafico-madrid"}}
{"idelem": "4740", "descripcion": "CJAL. FCO. J. JIMENEZ n.86 O-E (F. CALVO-ALHAMBRA)", "accesoAsociado": "240604", "intensidad": 180, "ocupacion": 3, "carga": 15, "nivelServici

In [14]:
ndjson

'{"index": {"_index" : "trafico-madrid"}}\n{"idelem": "3409", "descripcion": "SEPULVEDA n.118 N-S (CEBREROS-CJAL. FCO. J. JIMENEZ)", "accesoAsociado": "240102", "intensidad": 42, "ocupacion": 0, "carga": 1, "nivelServicio": 0, "intensidadSat": 3000, "error": "N", "subarea": "1718", "fecha_hora": "2023-04-13T17:30:05Z", "coordenadas": {"lat": 40.401447264855946, "lon": -3.7541516712567753}}\n{"index": {"_index" : "trafico-madrid"}}\n{"idelem": "4739", "descripcion": "CJAL. FCO. J. JIMENEZ n.126 E-O (BERLANAS-SEPULVEDA)", "accesoAsociado": "240101", "intensidad": 85, "ocupacion": 1, "carga": 7, "nivelServicio": 0, "intensidadSat": 1500, "error": "N", "subarea": "1718", "fecha_hora": "2023-04-13T17:30:05Z", "coordenadas": {"lat": 40.399707541055946, "lon": -3.7537194086223162}}\n{"index": {"_index" : "trafico-madrid"}}\n{"idelem": "4740", "descripcion": "CJAL. FCO. J. JIMENEZ n.86 O-E (F. CALVO-ALHAMBRA)", "accesoAsociado": "240604", "intensidad": 180, "ocupacion": 3, "carga": 15, "nivelS

In [15]:
url = "https://icai.es.europe-west2.gcp.elastic-cloud.com:9243/"
username = "admin"
password = "comillas"
index = "trafico-madrid"
headers = {"Content-Type": "application/json"}
api="""/_bulk"""

response = requests.post(url+index+api, data = ndjson, headers = headers, auth=(username, password))
response.json()


{'took': 364,
 'errors': True,
 'items': [{'index': {'_index': 'trafico-madrid',
    '_id': 'U4FMe4cBEzhJ8DaUOErF',
    '_version': 1,
    'result': 'created',
    '_shards': {'total': 2, 'successful': 2, 'failed': 0},
    '_seq_no': 292,
    '_primary_term': 1,
    'status': 201}},
  {'index': {'_index': 'trafico-madrid',
    '_id': 'VIFMe4cBEzhJ8DaUOErG',
    '_version': 1,
    'result': 'created',
    '_shards': {'total': 2, 'successful': 2, 'failed': 0},
    '_seq_no': 294,
    '_primary_term': 1,
    'status': 201}},
  {'index': {'_index': 'trafico-madrid',
    '_id': 'VYFMe4cBEzhJ8DaUOErG',
    '_version': 1,
    'result': 'created',
    '_shards': {'total': 2, 'successful': 2, 'failed': 0},
    '_seq_no': 295,
    '_primary_term': 1,
    'status': 201}},
  {'index': {'_index': 'trafico-madrid',
    '_id': 'VoFMe4cBEzhJ8DaUOErG',
    '_version': 1,
    'result': 'created',
    '_shards': {'total': 2, 'successful': 2, 'failed': 0},
    '_seq_no': 296,
    '_primary_term': 1,
    '